# TF-IDF From Scratch

Library Import

In [114]:
import pandas as pd
import numpy as np
import nltk
import string
import time
import scipy.sparse

from nltk import word_tokenize
from operator import itemgetter

In [115]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\user\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## Data Loading

Note that dataset can be found here: https://www.kaggle.com/tmdb/tmdb-movie-metadata

Read a csv file.

In [116]:
path = "tmdb_5000_movies.csv"
df = pd.read_csv(path)
df

budget                                             genres  \
0     237000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
1     300000000  [{"id": 12, "name": "Adventure"}, {"id": 14, "...   
2     245000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
3     250000000  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4     260000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
...         ...                                                ...   
4798     220000  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4799       9000  [{"id": 35, "name": "Comedy"}, {"id": 10749, "...   
4800          0  [{"id": 35, "name": "Comedy"}, {"id": 18, "nam...   
4801          0                                                 []   
4802          0                [{"id": 99, "name": "Documentary"}]   

                                               homepage      id  \
0                           http://www.avatarmovie.com/   19995   
1          http://disney.go.com/disneypictures/pirates/     285   
2           http://www.sonypictures.com/movies/spectre/  206647   
3                    http://www.thedarkknightrises.com/   49026   
4                  http://movies.disney.com/john-carter   49529   
...                                                 ...     ...   
4798                                                NaN    9367   
4799                                                NaN   72766   
4800  http://www.hallmarkchannel.com/signedsealeddel...  231617   
4801                        http://shanghaicalling.com/  126186   
4802                                                NaN   25975   

                                               keywords original_language  \
0     [{"id": 1463, "name": "culture clash"}, {"id":...                en   
1     [{"id": 270, "name": "ocean"}, {"id": 726, "na...                en   
2     [{"id": 470, "name": "spy"}, {"id": 818, "name...                en   
3     [{"id": 849, "name": "dc comics"}, {"id": 853,...                en   
4     [{"id": 818, "name": "based on novel"}, {"id":...                en   
...                                                 ...               ...   
4798  [{"id": 5616, "name": "united states\u2013mexi...                es   
4799                                                 []                en   
4800  [{"id": 248, "name": "date"}, {"id": 699, "nam...                en   
4801                                                 []                en   
4802  [{"id": 1523, "name": "obsession"}, {"id": 224...                en   

                                original_title  \
0                                       Avatar   
1     Pirates of the Caribbean: At World's End   
2                                      Spectre   
3                        The Dark Knight Rises   
4                                  John Carter   
...                                        ...   
4798                               El Mariachi   
4799                                 Newlyweds   
4800                 Signed, Sealed, Delivered   
4801                          Shanghai Calling   
4802                         My Date with Drew   

                                               overview  popularity  \
0     In the 22nd century, a paraplegic Marine is di...  150.437577   
1     Captain Barbossa, long believed to be dead, ha...  139.082615   
2     A cryptic message from Bond’s past sends him o...  107.376788   
3     Following the death of District Attorney Harve...  112.312950   
4     John Carter is a war-weary, former military ca...   43.926995   
...                                                 ...         ...   
4798  El Mariachi just wants to play his guitar and ...   14.269792   
4799  A newlywed couple's honeymoon is upended by th...    0.642552   
4800  "Signed, Sealed, Delivered" introduces a dedic...    1.444476   
4801  When ambitious New York attorney Sam is sent t...    0.857008   
4802  Ever since the second grade when he first saw ... 

List all fields

In [117]:
id_field = "id"
budget_field = "budget"
genres_field = "genres"
homepage_field = "homepage"
keyword_field = "keywords"
original_language_field = "original_language"
original_title_field = "original_title"
overview_field = "overview"
popularity_field = "popularity"
production_companies_field = "production_companies"
production_countries_field = "production_countries"
release_date_field = "release_date"
revenue_field = "revenue"
runtime_field = "runtime"
spoken_languages_field = "spoken_languages"
status_field = "status"
tagline_field = "tagline"
title_field = "title"
vote_average_field = "vote_average"
vote_count_field = "vote_count"

Define Fields

Note that we also remove unecessary fields

In [118]:
fields = df.columns.to_list()
target = original_title_field

fields.remove(id_field)
fields.remove(homepage_field)
fields.remove(title_field)
fields.remove(original_title_field)
fields.remove(revenue_field)
fields.remove(vote_count_field)

print(fields)

['budget', 'genres', 'keywords', 'original_language', 'overview', 'popularity', 'production_companies', 'production_countries', 'release_date', 'runtime', 'spoken_languages', 'status', 'tagline', 'vote_average']


In [119]:
df[fields].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4803 entries, 0 to 4802
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   budget                4803 non-null   int64  
 1   genres                4803 non-null   object 
 2   keywords              4803 non-null   object 
 3   original_language     4803 non-null   object 
 4   overview              4800 non-null   object 
 5   popularity            4803 non-null   float64
 6   production_companies  4803 non-null   object 
 7   production_countries  4803 non-null   object 
 8   release_date          4802 non-null   object 
 9   runtime               4801 non-null   float64
 10  spoken_languages      4803 non-null   object 
 11  status                4803 non-null   object 
 12  tagline               3959 non-null   object 
 13  vote_average          4803 non-null   float64
dtypes: float64(3), int64(1), object(10)
memory usage: 525.5+ KB


In [120]:
df[fields].describe()

budget   popularity      runtime  vote_average
count  4.803000e+03  4803.000000  4801.000000   4803.000000
mean   2.904504e+07    21.492301   106.875859      6.092172
std    4.072239e+07    31.816650    22.611935      1.194612
min    0.000000e+00     0.000000     0.000000      0.000000
25%    7.900000e+05     4.668070    94.000000      5.600000
50%    1.500000e+07    12.921594   103.000000      6.200000
75%    4.000000e+07    28.313505   118.000000      6.800000
max    3.800000e+08   875.581305   338.000000     10.000000

## Data Preprocessing

### Convert Number Fields to Word

In [121]:
def budget_to_string(row):
    if row >= 5000000:
        return "expensive"
    else:
        return "cheap"

def popularity_to_string(row):
    if row >= 12:
        return "Popular"
    else:
        return "Rare"

def runtime_to_string(row):
    if row >= 94:
        return "Long"
    else:
        return "Short"

def vote_average_to_string(row):
    if row >= 7.5:
        return "Good"
    elif row > 5.6 and row < 7.5:
        return "Average"
    else:
        return "Poor"

number_to_word_converted_df = df[fields].copy()

number_to_word_converted_df[budget_field] = number_to_word_converted_df[budget_field].apply(budget_to_string)
number_to_word_converted_df[popularity_field] = number_to_word_converted_df[popularity_field].apply(popularity_to_string)
number_to_word_converted_df[runtime_field] = number_to_word_converted_df[runtime_field].apply(runtime_to_string)
number_to_word_converted_df[vote_average_field] = number_to_word_converted_df[vote_average_field].apply(vote_average_to_string)

number_to_word_converted_df.loc[8, :]

budget                                                          expensive
genres                  [{"id": 12, "name": "Adventure"}, {"id": 14, "...
keywords                [{"id": 616, "name": "witch"}, {"id": 2343, "n...
original_language                                                      en
overview                As Harry begins his sixth year at Hogwarts, he...
popularity                                                        Popular
production_companies    [{"name": "Warner Bros.", "id": 6194}, {"name"...
production_countries    [{"iso_3166_1": "GB", "name": "United Kingdom"...
release_date                                                   2009-07-07
runtime                                                              Long
spoken_languages                 [{"iso_639_1": "en", "name": "English"}]
status                                                           Released
tagline                                             Dark Secrets Revealed
vote_average                          

### Convert JSON in fields of Movie Dataset into string

In [122]:
def convert_json_field_in_df_into_strings(df, df_field, json_field):
    import json
    
    """
    Convert JSON fields to string, by taking the dataframe and a field, a json field, which returns a list of string

    from a specific field in a dataframe

    Below are the explanation of parameters used.
    * df: dataframe to be used
    * df_field: field in dataframe, to convert json into strings
    * json_field: one field to be kept from json inside the data field in dataframe.

    Consider the example:

    | id | movie_name | movie_genres |

    | 1 | a           | {"id": 1, "name": "action"}, {"id": 2, "name": "romance"} | 

    | 2 | b           | {"id": 1, "name": "slice of life"}, {"id": 2, "name": "food"} |

    If we use the function: 
    
    convert_json_field_in_df_into_strings(df, "movie_genres", "name")

    This gives us the list of string from all rows in movie_genres field.

    """

    json_data = json.loads(df[df_field].to_json())
    json_values = list(json_data.values())

    list_of_strings = []

    for value in json_values:

        my_string = ""

        dicts = list(json.loads(value))[:]

        for dict_value in dicts:
            my_string += f"{dict_value[json_field]} "
        list_of_strings.append(my_string[:-1])

    return list_of_strings

In [123]:
json_converted_df = number_to_word_converted_df.copy()

json_field = "name"

json_converted_df[genres_field] = convert_json_field_in_df_into_strings(json_converted_df, genres_field, json_field)
json_converted_df[keyword_field] = convert_json_field_in_df_into_strings(json_converted_df, keyword_field, json_field)
json_converted_df[spoken_languages_field] = convert_json_field_in_df_into_strings(json_converted_df, spoken_languages_field, json_field)
json_converted_df[production_companies_field] = convert_json_field_in_df_into_strings(json_converted_df, production_companies_field, json_field)
json_converted_df[production_countries_field] = convert_json_field_in_df_into_strings(json_converted_df, production_countries_field, json_field)

json_converted_df.head(3)

budget                                    genres  \
0  expensive  Action Adventure Fantasy Science Fiction   
1  expensive                  Adventure Fantasy Action   
2  expensive                    Action Adventure Crime   

                                            keywords original_language  \
0  culture clash future space war space colony so...                en   
1  ocean drug abuse exotic island east india trad...                en   
2  spy based on novel secret agent sequel mi6 bri...                en   

                                            overview popularity  \
0  In the 22nd century, a paraplegic Marine is di...    Popular   
1  Captain Barbossa, long believed to be dead, ha...    Popular   
2  A cryptic message from Bond’s past sends him o...    Popular   

                                production_companies  \
0  Ingenious Film Partners Twentieth Century Fox ...   
1  Walt Disney Pictures Jerry Bruckheimer Films S...   
2                       Columbia Pictures Danjaq B24   

                      production_countries release_date runtime  \
0  United States of America United Kingdom   2009-12-10    Long   
1                 United States of America   2007-05-19    Long   
2  United Kingdom United States of America   2015-10-26    Long   

                            spoken_languages    status  \
0                            English Español  Released   
1                                    English  Released   
2  Français English Español Italiano Deutsch  Released   

                                          tagline vote_average  
0                     Enter the World of Pandora.      Average  
1  At the end of the world, the adventure begins.      Average  
2                           A Plan No One Escapes      Average

### Combine all df rows and columns into array of strings.

In [124]:
def get_removed_duplicated_space_in_string(my_string):
    return " ".join(my_string.split())

def combine_all_strings_from_df(df, fields, whitespace_split = ','):
    """
    Combine all strings from one df and all fields. 
    
    If you'd like to put something between words, provide whitespace_split parameter.
    """
    df_strings = df.to_string(header = False,
                       index = False,
                       columns = fields,
                       index_names = False).split('\n')

    all_strings = [get_removed_duplicated_space_in_string(s) for s in df_strings]

    return all_strings

df_strings = combine_all_strings_from_df(json_converted_df, fields)

print(df_strings[38])

expensive Action Adventure Fantasy obsession marvel comic sequel based on comic book electrocution medical experiment electricity super powers en For Peter Parker, life is busy. Between taking out the bad guys as Spider-Man and spending time with the person he loves, Gwen Stacy, high school graduation cannot come quickly enough. Peter has not forgotten about the promise he made to Gwen’s father to protect her by staying away, but that is a promise he cannot keep. Things will change for Peter when a new villain, Electro, emerges, an old friend, Harry Osborn, returns, and Peter uncovers new clues about his past. Popular Columbia Pictures Marvel Enterprises Avi Arad Productions Matt Tolmach Productions United States of America 2014-04-16 Long English Released No more secrets. Average


In [125]:
def get_erased_punctuations(text):
    list_of_punctuations = string.punctuation + "’‘"
    final_text = text
    
    for punc in list_of_punctuations:
        final_text = final_text.replace(punc, " ")
    
    final_text = get_removed_duplicated_space_in_string(final_text)
    
    return final_text

erased_punc_df_strings = [get_erased_punctuations(my_string) for my_string in df_strings]
erased_punc_df_strings[38]

'expensive Action Adventure Fantasy obsession marvel comic sequel based on comic book electrocution medical experiment electricity super powers en For Peter Parker life is busy Between taking out the bad guys as Spider Man and spending time with the person he loves Gwen Stacy high school graduation cannot come quickly enough Peter has not forgotten about the promise he made to Gwen s father to protect her by staying away but that is a promise he cannot keep Things will change for Peter when a new villain Electro emerges an old friend Harry Osborn returns and Peter uncovers new clues about his past Popular Columbia Pictures Marvel Enterprises Avi Arad Productions Matt Tolmach Productions United States of America 2014 04 16 Long English Released No more secrets Average'

## TF-IDF

### Word to Index Mapping

Populate into text mapping, so we know which word maps to which columns in our TF-IDF matrix.

In [128]:
def convert_set_to_indexed_dict(current_set):
    indexed_dict = {}

    for index, value in enumerate(current_set):
        indexed_dict[index] = value
    
    return indexed_dict

def convert_set_to_words_dict(current_set):
    indexed_dict = {}

    for index, value in enumerate(current_set):
        indexed_dict[value] = index
    
    return indexed_dict

def word_to_index_mapping(list_of_documents):
    all_unique_tokenized_words = set()

    for d in list_of_documents:
        tokenized_sentences = d.split(' ')
        all_unique_tokenized_words.update(tokenized_sentences)

    word_to_index_mapping = convert_set_to_indexed_dict(all_unique_tokenized_words)
    return word_to_index_mapping

def dict_head(dictionary, max_index = 5):
    print(list(dictionary.items())[:max_index])

df_word_to_index_dict = word_to_index_mapping(erased_punc_df_strings)

dict_head(df_word_to_index_dict, 3)

[(0, 'ethics'), (1, 'Giulia'), (2, 'places…')]


### Count Vectorizer

In [129]:
def custom_count_vectorizer(unique_words, documents):
    unique_values_to_count = list(unique_words.values())
    index_to_word_mapping = convert_set_to_words_dict(unique_words.values())

    itemgetter(*["Bonds"])(index_to_word_mapping)

    number_of_documents = len(documents)
    total_unique_values_to_count = len(unique_values_to_count)

    total_words_in_documents = scipy.sparse.lil_matrix(
        (number_of_documents, total_unique_values_to_count)
    )
    index = 0
    
    for index, d in enumerate(documents):
        words = d.split(' ')

        (unique_words_in_document, unique_word_counts) = np.unique(words, return_counts = True)
        print(unique_words_in_document)

        # total_words_in_documents.loc[index, unique_words_in_document] = unique_word_counts
        word_indexes_to_increment = itemgetter(*unique_words_in_document)(index_to_word_mapping)
        print(word_indexes_to_increment)

        total_words_in_documents[index, word_indexes_to_increment] = unique_word_counts
        print(index, end = " ")
        index += 1

custom_count_vectorizer(df_word_to_index_dict, erased_punc_df_strings)

['10' '12' '2009' '22nd' '3d' 'Action' 'Adventure' 'America' 'Average'
 'Century' 'Corporation' 'Dune' 'English' 'Enter' 'Entertainment'
 'Español' 'Fantasy' 'Fiction' 'Film' 'Fox' 'In' 'Ingenious' 'Kingdom'
 'Lightstorm' 'Long' 'Marine' 'Pandora' 'Partners' 'Popular' 'Released'
 'Science' 'States' 'Twentieth' 'United' 'World' 'a' 'affair' 'alien' 'an'
 'and' 'anti' 'battle' 'becomes' 'between' 'but' 'century' 'cgi'
 'civilization' 'clash' 'colony' 'culture' 'dispatched' 'en' 'expensive'
 'following' 'future' 'futuristic' 'is' 'love' 'marine' 'mind' 'mission'
 'moon' 'of' 'on' 'orders' 'paraplegic' 'planet' 'power' 'protecting'
 'relations' 'romance' 'society' 'soldier' 'soul' 'space' 'the' 'to'
 'torn' 'travel' 'tribe' 'unique' 'war']
(5791, 25634, 610, 11212, 20040, 29947, 6707, 30806, 19931, 25076, 22700, 30625, 10519, 10239, 27716, 23473, 13620, 20396, 5979, 18802, 9506, 24829, 849, 27566, 20799, 24371, 10003, 22521, 7722, 7079, 12976, 28792, 13263, 17723, 10127, 20842, 11977, 3013